In [6]:
# import pandas as pd
# import numpy as np
# import matplotlib.pyplot as plt
# import seaborn as sns
# from geopy.geocoders import Nominatim
# import geopy.distance
# from geopy.extra.rate_limiter import RateLimiter
# import json
# import 
# import os
# import folium
# import geopandas as gpd
# import fiona
# import shapefile as shp
# from difflib import SequenceMatcher
# from shapely.geometry import Point, Polygon
# from geopandas import GeoDataFrame

In [7]:
import folium
import numpy as np
from sklearn.preprocessing import minmax_scale
from collections import defaultdict, OrderedDict
import geopandas as gpd
import pandas as pd
from folium.plugins import HeatMapWithTime

In [8]:
member_use=pd.read_csv("Usage/member_usage_start")
member_use
member_use.drop(["Unnamed: 0"],axis=1,inplace=True)
member_use.rename(columns={"0":"count"},inplace=True)
member_use["count"]=minmax_scale(member_use["count"])
casual_use=pd.read_csv("Usage/casual_usage_start")
casual_use.drop(["Unnamed: 0"],axis=1,inplace=True)
casual_use.rename(columns={"0":"count"},inplace=True)
casual_use["count"]=minmax_scale(casual_use["count"])
#Dictionary for {month:(station,usage)} for 2011
member_heat=defaultdict(list)
for r in member_use.itertuples():
    member_heat[r.month].append([r.lat,r.long,r.count])
member_heat_start=OrderedDict(sorted(member_heat.items()))
#Dictionary for {month:(station,usage)} for 2012
casual_heat=defaultdict(list)
for r in casual_use.itertuples():
    casual_heat[r.month].append([r.lat,r.long,r.count])
casual_heat_start=OrderedDict(sorted(casual_heat.items()))

In [9]:
member_use=pd.read_csv("Usage\member_usage_end")
member_use
member_use.drop(["Unnamed: 0"],axis=1,inplace=True)
member_use.rename(columns={"0":"count"},inplace=True)
member_use["count"]=minmax_scale(member_use["count"])
casual_use=pd.read_csv("Usage\casual_usage_end")
casual_use.drop(["Unnamed: 0"],axis=1,inplace=True)
casual_use.rename(columns={"0":"count"},inplace=True)
casual_use["count"]=minmax_scale(casual_use["count"])
#Dictionary for {month:(station,usage)} for 2011
member_heat=defaultdict(list)
for r in member_use.itertuples():
    member_heat[r.month].append([r.lat,r.long,r.count])
member_heat_end=OrderedDict(sorted(member_heat.items()))
#Dictionary for {month:(station,usage)} for 2012
casual_heat=defaultdict(list)
for r in casual_use.itertuples():
    casual_heat[r.month].append([r.lat,r.long,r.count])
casual_heat_end=OrderedDict(sorted(casual_heat.items()))

In [11]:
#Census information for DC
geo_dc=gpd.read_file(r"D:\CAB_Work\Project_3\map\Census_2010_DC.geojson")
pop_dc=[]
pop_dc=pd.DataFrame(pop_dc)
pop_dc["geoid"]=0
pop_dc["population"]=0
pop_dc["population"]=geo_dc["P0010001"]
pop_dc["geoid"]=geo_dc["TRACT"]
drop_list=["TRACT","geometry"]
geo_dc=geo_dc.drop(geo_dc.columns.difference(drop_list),axis=1)
geo_dc.rename(columns={"TRACT":"geoid"},inplace=True)
#Census information for Virginia. Due to the fact that population breakdown is in county level and not lower, a comparison with DC is not feasible
pop_virginia=pd.read_csv(r"D:\CAB_Work\Project_3\map\Census_2010_Virginia.csv")
pop_virginia.columns=pop_virginia.columns.str.replace(" ","_")
pop_virginia.rename(columns={"B01003_001E":"population","county_1":"geoid"},inplace=True)
pop_virginia=pop_virginia.loc[(pop_virginia["geoid"]==13)|(pop_virginia["county"]=="Alexandria city, Virginia")]
pop_virginia=pop_virginia.loc[(pop_virginia["year"]==2011)]
drop_list=["population","geoid"]
pop_virginia=pop_virginia.drop(pop_virginia.columns.difference(drop_list),axis=1)
pop_virginia["geoid"]=pop_virginia["geoid"].replace({13:51013,510:51510})
geo_virginia=gpd.read_file(r"D:\CAB_Work\Project_3\map\Land_Virginia.geojson")
geo_virginia["geoid"]=geo_virginia["geoid"].str[:5]
geo_virginia=geo_virginia.loc[(geo_virginia["geoid"]=="51013")|(geo_virginia["geoid"]=="51510")]
drop_list=["geoid","geometry"]
geo_virginia=geo_virginia.drop(geo_virginia.columns.difference(drop_list),axis=1)
#Metro network map
metro_lines=gpd.read_file(r"D:\CAB_Work\Project_3\map\Metro_Lines.geojson")
#Park and ride stations
park=gpd.read_file(r"D:\CAB_Work\Project_3\map\Park_and_Ride_Points.geojson")

In [21]:
geo_dc

geoid                                           geometry
0    002102  POLYGON ((-77.01188 38.96017, -77.01214 38.960...
1    009508  POLYGON ((-76.99438 38.95728, -76.99534 38.957...
2    001200  POLYGON ((-77.06819 38.95221, -77.06875 38.953...
3    009503  POLYGON ((-76.98613 38.95262, -76.98624 38.952...
4    009501  POLYGON ((-77.00784 38.95195, -77.00784 38.952...
..      ...                                                ...
174  009801  POLYGON ((-76.99413 38.83756, -76.99419 38.837...
175  009802  POLYGON ((-76.99091 38.83236, -76.99107 38.832...
176  009810  POLYGON ((-77.00334 38.83097, -77.00338 38.830...
177  009811  POLYGON ((-77.00057 38.83097, -77.00069 38.830...
178  010900  POLYGON ((-77.00600 38.82410, -77.00603 38.824...

[179 rows x 2 columns]

In [13]:
m=folium.Map(location=[38.900497,-77.007507],zoom_start=12,min_zoom=11,zoom_control=False,Control_scale=True)
fg1=folium.FeatureGroup(name="Metro Network",show=False)
fg2=folium.FeatureGroup(name="Bike Lanes",show=False)
fg4=folium.FeatureGroup(name="Park and Ride stations",show=False)
folium.Choropleth(geo_data=geo_dc,data=pop_dc,columns=["geoid","population"],key_on="feature.properties.geoid",
    fill_color="YlGnBu",name="Population density",fill_opacity=0.6,line_opacity=0.2,show=False).add_to(m)
m.add_child(fg1)
m.add_child(fg2)
m.add_child(fg4)
HeatMapWithTime(data=list(member_heat_start.values()),index=list(member_heat_start.keys()),show=False,radius=30,min_opacity=0.2,max_opacity=1,name="Member usage Starting stations").add_to(m)
HeatMapWithTime(data=list(casual_heat_start.values()),index=list(casual_heat_start.keys()),show=False,radius=30,min_opacity=0.2,max_opacity=1,name="Casual usage Starting stations").add_to(m)
HeatMapWithTime(data=list(member_heat_end.values()),index=list(member_heat_end.keys()),show=False,radius=30,min_opacity=0.2,max_opacity=1,name="Member usage Ending stations").add_to(m)
HeatMapWithTime(data=list(casual_heat_end.values()),index=list(casual_heat_end.keys()),show=False,radius=30,min_opacity=0.2,max_opacity=1,name="Casual usage Ending stations").add_to(m)
for i in range(len(park)):
    fg4.add_child(folium.CircleMarker(location=[park.loc[i,"geometry"].y,park.loc[i,"geometry"].x],popup=park.loc[i,"NAME"],color="red",radius=5))
folium.GeoJson(r"D:\CAB_Work\Project_3\map\Metro_Lines.geojson").add_to(fg1)
folium.GeoJson(r"D:\CAB_Work\Project_3\map\Signed_Bike_Routes.geojson").add_to(fg2)
folium.GeoJson(r"D:\CAB_Work\Project_3\map\Bike_Trails.geojson").add_to(fg2)
folium.GeoJson(r"D:\CAB_Work\Project_3\map\Metro_Stations.geojson").add_to(fg1)
folium.LayerControl().add_to(m)
m.save(outfile="test.html")
m